# **Weatherdata Visualization**

In [ ]:
# This is the fully automated version, where only some answers need to be answered at the beginning. The rest of the code is to no interest and can just be run all at once.
# next step to do a step by step code for workshops

In [12]:
import datetime

options = ['temperature', 'relative humidity', 'wind', 'rain', 'low clouds', 'high clouds', 'snow']
color_palettes = ['viridis', 'plasma', 'inferno', 'magma', 'cividis']
valid_years = range(1981, 2016)  # range of valid years
yes_no_options = ['yes', 'no']
each_specific = ['each', 'specific']
hours_of_day = ['0', '3', '6', '9', '12', '15', '18', '21']
lat_range = range(-90, 91)
lon_range = range(-180, 181)

def get_valid_input(prompt, valid_options):
    while True:
        user_input = input(prompt).strip()
        try:
            if isinstance(valid_options, range):
                user_input = int(user_input)
            if user_input in valid_options:
                return user_input
        except ValueError:
            pass
        print(f"Invalid input. Please choose from: {', '.join(map(str, valid_options))}")

def get_valid_date(prompt):
    while True:
        user_input = input(prompt).strip()
        try:
            month, day = map(int, user_input.split('-'))
            date = datetime.datetime(2022, month, day)  # Using a non-leap year to validate month-date
            return date, f"{month:02d}-{day:02d}"
        except ValueError:
            print("Invalid date. Please enter a valid date in MM-DD format.")

def ask_advanced_settings():

    lat_min = get_valid_input("Enter latitude min (-90 to 90): ", lat_range)
    while True:
        lat_max = get_valid_input("Enter latitude max ("+str(lat_min)+" to 90): ", lat_range)
        if lat_max > lat_min:
            break
        else:
            print("Latitude max must be greater than latitude min. Please enter valid values.")

    lon_min = get_valid_input("Enter longitude min (-180 to 180): ", lon_range)
    while True:
        lon_max = get_valid_input("Enter longitude max ("+str(lon_min)+" to 180): ", lon_range)
        if lon_max > lon_min:
            break
        else:
            print("Longitude max must be greater than longitude min. Please enter valid values.")

    axis = get_valid_input("Do you want to plot with axis or not (yes/no): ", yes_no_options)
    specific_hour = get_valid_input("Do you want to plot each time step or a specific hour of the day (each/specific): ", each_specific)
    hour = None
    if specific_hour == 'specific':
        hour = get_valid_input("Which hour of the day (0, 3, 6, 9, 12, 15, 18, 21): ", hours_of_day)
        hour = int(hour)

    save = get_valid_input("Do you want to save the animation as .mp4 (yes/no) :", yes_no_options)
    return lat_min, lat_max, lon_min, lon_max, hour, axis, save

# Initial inputs
variable_prompt = f"Choose a variable ({', '.join(options)}): "
year_prompt = f"Choose a year ({min(valid_years)}-{max(valid_years)}): "
start_date_prompt = "Enter start date (MM-DD): "
end_date_prompt = "Enter end date (MM-DD): "
color_palette_prompt = f"Choose a color palette ({', '.join(color_palettes)}): "
world_map_prompt = "With world map plotted on the data? (yes/no): "

variable = get_valid_input(variable_prompt, options)
year = get_valid_input(year_prompt, valid_years)
start_date_dt, start_date_str = get_valid_date(start_date_prompt)
while True:
    end_date_dt, end_date_str = get_valid_date(end_date_prompt)
    if end_date_dt > start_date_dt:
        break
    else:
        print("End date must be after the start date. Please enter a valid end date.")

color_palette = get_valid_input(color_palette_prompt, color_palettes)
world_map = get_valid_input(world_map_prompt, yes_no_options)

# Advanced settings
advanced_settings_prompt = "Do you want to change any special settings? (yes/no): "
advanced_settings = get_valid_input(advanced_settings_prompt, yes_no_options)

if advanced_settings == 'yes':
    lat_min, lat_max, lon_min, lon_max, hour, axis, save = ask_advanced_settings()
else:
    lat_min, lat_max, lon_min, lon_max, hour, axis = -90, 90, -180, 179,  'no','no'

print(f"You chose: {variable} with the color palette: {color_palette} for the year: {year}, world map plotted: {world_map}, start date: {start_date_str}, end date: {end_date_str}")
if advanced_settings == 'yes':
    print(f"Advanced settings: lat_min={lat_min}, lat_max={lat_max}, lon_min={lon_min}, lon_max={lon_max}, specific hour={hour}, axis={axis}")
else:
    print("No advanced settings chosen.")


Choose a variable (temperature, relative humidity, wind, rain, low clouds, high clouds, snow): snow
Choose a year (1981-2015): 1997
Enter start date (MM-DD): 01-01
Enter end date (MM-DD): 01-05
Choose a color palette (viridis, plasma, inferno, magma, cividis): magma
With world map plotted on the data? (yes/no): yes
Do you want to change any special settings? (yes/no): no
You chose: snow with the color palette: magma for the year: 1997, world map plotted: yes, start date: 01-01, end date: 01-05
No advanced settings chosen.


In [13]:
# load the required packages
# Check if cartopy is installed and install it if not
try:
    import cartopy
    print("Cartopy is already installed.")
except ImportError:
    print("Cartopy is not installed. Installing now...")
    !pip install cartopy
    import cartopy
    print("Cartopy has been installed.")

import os
import requests
import xarray as xr
import matplotlib.pyplot as plt
import urllib.request
import glob
import matplotlib.animation as animation
import numpy as np
from IPython.display import HTML
import warnings
import cartopy.crs as ccrs
import cartopy.feature as cfeature

Cartopy is not installed. Installing now...
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.7/11.7 MB 55.1 MB/s eta 0:00:00
Cartopy has been installed.


In [14]:
# download the data

### here you have to comment or uncomment the dataset you want to use
# 3 examples of datasets to download

# MO-datasets from 1981-2015

## 2m air temperature
if variable == 'temperature':
  dataset = 'air.2m.'+str(year)+'.nc' ### insert the name of the dataset you want to download
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/2mMO/'+dataset ### copy and paste the url of the dataset

## wind in north-south direction
if variable == 'wind':
  dataset = 'vwnd.10m.'+str(year)+'.nc'
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/10mMO/'+dataset

## relative humidity
if variable == 'relative humidity':
  dataset = 'rhum.2m.'+str(year)+'.nc'
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/2mMO/'+dataset

## rain
if variable == 'rain':
  dataset = 'crain.'+str(year)+'.nc'
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/sfcMO/'+dataset

## total low cloud cover
if variable == 'low clouds':
  dataset = 'tcdc.lowcld.'+str(year)+'.nc'
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/cldLyrMO/'+dataset

## total high cloud cover
if variable == 'high clouds':
  dataset = 'tcdc.topcld.'+str(year)+'.nc'
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/cldLyrMO/'+dataset

## snow
if variable == 'snow':
  dataset = 'snowc.'+str(year)+'.nc'
  url = f'https://downloads.psl.noaa.gov/Datasets/20thC_ReanV3/sfcMO/'+dataset


# # Check if the dataset already exists
# if not os.path.exists(dataset):
#     print(f"{dataset} does not exist. Downloading...")
#     urllib.request.urlretrieve(url, dataset)
#     print(f"Downloaded {dataset}")
# else:
#     print(f"{dataset} already exists. Skipping download.")

# Check if the dataset already exists locally
if not os.path.exists(dataset):
    print(f"{dataset} does not exist. Downloading into RAM...")
    response = urllib.request.urlopen(url)
    data = response.read()  # Read the data into memory
    data_in_memory = io.BytesIO(data)  # Create an in-memory file-like object
    print(f"Downloaded {dataset} into RAM.")
else:
    print(f"{dataset} already exists. Skipping download.")



snowc.1997.nc does not exist. Downloading into RAM...
Downloaded snowc.1997.nc into RAM.


In [18]:
# open the downloaded dataset
ds = xr.open_dataset(data_in_memory)
data_variable = ds[list(ds.keys())[0]]
if isinstance(hour, int):
    data_variable = data_variable.sel(time=ds['time'].dt.hour == [hour])

start_time = str(year)+'-'+start_date_str
end_time = str(year)+'-'+end_date_str
data_variable = data_variable.sel(time=slice(start_time, end_time))

# as seen on the picture above the data has it's middle in the pacific, but we want to have an atlantic-centered plot
data_variable_west = data_variable[:,:,180:]
data_variable_east = data_variable[:,:,0:180]
data_variable_aligned = xr.concat([data_variable_west, data_variable_east], dim = 'lon')

lat = data_variable['lat']
data_variable['lon'] = range(-180,180)
lon = data_variable['lon']


In [16]:
lon_min = -180
lon_max = 179
lat_min = -90
lat_max = 89
save = 'no'

In [17]:
# Create a figure with a cartopy projection
fig, ax = plt.subplots(figsize=(10, 6),subplot_kw={'projection': ccrs.PlateCarree()})
# Define how long each time step will be displayed in animation
interval = 80  # in milliseconds
plt.rcParams['animation.embed_limit'] = 50  # Increase the limit to 50 MB
# Create a ScalarMappable and add a colorbar
sm = plt.cm.ScalarMappable(cmap=color_palette, norm=plt.Normalize(vmin=data_variable_aligned.min(), vmax=data_variable_aligned.max()))
sm._A = []  # ScalarMappable needs an array, but we only use it for the colorbar
cbar = fig.colorbar(sm, ax=ax, orientation='vertical', fraction=0.02, pad=0.04)
cbar.set_label(data_variable_aligned.attrs['units'])

def animate_map(frame):

    # Clear the previous plot
    ax.clear()

    if world_map == 'yes':

      ax.set_extent([lon_min, lon_max, lat_min, lat_max], crs=ccrs.PlateCarree())
      ax.coastlines()
      ax.add_feature(cfeature.BORDERS, linestyle='-')

    img = ax.imshow(data_variable_aligned[frame, np.where(lat == lat_min)[0][0]:np.where(lat == lat_max)[0][0], np.where(lon == lon_min)[0][0]:np.where(lon == lon_max)[0][0]],
                    extent=[lon_min,lon_max,lat_min,lat_max], cmap=color_palette, origin='lower', transform=ccrs.PlateCarree())
    # img = ax.imshow(data_variable_aligned[frame, :, :], extent=[-180, 180, -90, 90],
    #                 cmap=color_palette, origin='lower', transform=ccrs.PlateCarree())
    ax.set_title(str(data_variable['time'][frame].values).split('.')[0] + '     ' + data_variable_aligned.attrs['long_name'])


    if axis == 'yes':
      # Set axis labels and ticks
      ax.set_xlabel('Longitude')
      ax.set_ylabel('Latitude')
      ax.set_xticks(np.linspace(lon_min, lon_max, num=5))  # Adjust the number of ticks as needed
      ax.set_yticks(np.linspace(lat_min, lat_max, num=5))  # Adjust the number of ticks as needed
      # Show grid lines
      ax.gridlines(draw_labels=False, linewidth=0.5, color='gray', linestyle='--')

    if axis == 'no':
      # Remove axis ticks and labels
      ax.set_xticks([])
      ax.set_yticks([])

plt.close(fig)

ani = animation.FuncAnimation(fig, animate_map, frames=len(data_variable['time']), interval=interval, blit=False)


if save == 'yes':
  ani.save(variable+'_'+str(year)+'_animation.mp4', writer='ffmpeg', fps=10)
else:
  display(HTML(ani.to_jshtml()))

/usr/local/lib/python3.10/dist-packages/cartopy/io/__init__.py:241: DownloadWarning: Downloading: https://naturalearth.s3.amazonaws.com/110m_physical/ne_110m_coastline.zip
  warnings.warn(f'Downloading: {url}', DownloadWarning)
/usr/local/lib/python3.10/dist-packages/cartopy/io/__init__.py:241: DownloadWarning: Downloading: https://naturalearth.s3.amazonaws.com/110m_cultural/ne_110m_admin_0_boundary_lines_land.zip
  warnings.warn(f'Downloading: {url}', DownloadWarning)
